# End-to-End Python Project: Retail Orders Analysis

In this project, we perform an end-to-end data analysis of a retail orders dataset. We'll clean and transform the data, create a Spark DataFrame, and run SQL queries to extract meaningful insights.

### 1. Install Necessary Libraries and Download the Dataset

In [0]:
!pip install kaggle

  Using cached kaggle-1.6.17-py3-none-any.whl
  Using cached python_slugify-8.0.4-py2.py3-none-any.whl (10 kB)
  Using cached tqdm-4.66.5-py3-none-any.whl (78 kB)
  Using cached certifi-2024.8.30-py3-none-any.whl (167 kB)
  Using cached text_unidecode-1.3-py2.py3-none-any.whl (78 kB)
  Attempting uninstall: certifi
    Found existing installation: certifi 2021.10.8
    Not uninstalling certifi at /databricks/python3/lib/python3.9/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-6143b686-463f-4664-b710-3beaa3eb6343
    Can't uninstall 'certifi'. No files were found to uninstall.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-6143b686-463f-4664-b710-3beaa3eb6343/bin/python -m pip install --upgrade pip' command.


In [0]:
!kaggle datasets download -d ankitbansal06/retail-orders

Dataset URL: https://www.kaggle.com/datasets/ankitbansal06/retail-orders
License(s): CC0-1.0
  0%|                                                | 0.00/200k [00:00<?, ?B/s]
100%|████████████████████████████████████████| 200k/200k [00:00<00:00, 7.65MB/s]


### 2. Extract the Dataset
We extract the dataset from the downloaded zip file using the ZipFile module.

In [0]:
from zipfile import ZipFile
dataset = '/databricks/driver/retail-orders.zip'

with ZipFile(dataset,'r') as zip:
  zip.extractall()
  print('The dataset is extracted')

The dataset is extracted


###3. Load the Dataset into a Pandas DataFrame
We load the dataset into a Pandas DataFrame and handle missing values using na_values.

In [0]:
import pandas as pd

In [0]:
df_orders = pd.read_csv('/databricks/driver/orders.csv',na_values=['Not Available', 'unknown'])

### 4. Data Cleaning and Transformation
We perform data cleaning and transformation by taking the following steps:

- **Replace spaces with underscores** in column names to make them easier to reference in code.
- **Convert column names to lowercase** for consistency and to avoid case sensitivity issues.
- **Calculate additional columns**:
  - **Discount**: Calculated as `list_price * discount_percent * 0.01`.
  - **Sale Price**: Derived by subtracting the discount from the list price (`list_price - discount`).
  - **Profit**: Calculated by subtracting the cost price from the sale price (`sale_price - cost_price`).


In [0]:
df_orders['Ship Mode'].unique()

Out[11]: array(['Second Class', 'Standard Class', nan, 'First Class', 'Same Day'],
      dtype=object)

In [0]:
df_orders.columns=df_orders.columns.str.replace(' ','_')

In [0]:
df_orders.columns = df_orders.columns.str.lower()

In [0]:
df_orders

order_id 
 order_date 
 ship_mode 
 segment 
 country 
 city 
 state 
 postal_code 
 region 
 category 
 sub_category 
 product_id 
 cost_price 
 list_price 
 quantity 
 discount_percent 
 
 
 
 
 0 
 1 
 2023-03-01 
 Second Class 
 Consumer 
 United States 
 Henderson 
 Kentucky 
 42420 
 South 
 Furniture 
 Bookcases 
 FUR-BO-10001798 
 240 
 260 
 2 
 2 
 
 
 1 
 2 
 2023-08-15 
 Second Class 
 Consumer 
 United States 
 Henderson 
 Kentucky 
 42420 
 South 
 Furniture 
 Chairs 
 FUR-CH-10000454 
 600 
 730 
 3 
 3 
 
 
 2 
 3 
 2023-01-10 
 Second Class 
 Corporate 
 United States 
 Los Angeles 
 California 
 90036 
 West 
 Office Supplies 
 Labels 
 OFF-LA-10000240 
 10 
 10 
 2 
 5 
 
 
 3 
 4 
 2022-06-18 
 Standard Class 
 Consumer 
 United States 
 Fort Lauderdale 
 Florida 
 33311 
 South 
 Furniture 
 Tables 
 FUR-TA-10000577 
 780 
 960 
 5 
 2 
 
 
 4 
 5 
 2022-07-13 
 Standard Class 
 Consumer 
 United States 
 Fort Lauderdale 
 Florida 
 33311 
 South 
 Office Supplies 
 Storage 
 OFF-ST-10000760 
 20 
 20 
 2 
 5 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 9989 
 9990 
 2023-02-18 
 Second Class 
 Consumer 
 United States 
 Miami 
 Florida 
 33180 
 South 
 Furniture 
 Furnishings 
 FUR-FU-10001889 
 30 
 30 
 3 
 4 
 
 
 9990 
 9991 
 2023-03-17 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Furniture 
 Furnishings 
 FUR-FU-10000747 
 70 
 90 
 2 
 4 
 
 
 9991 
 9992 
 2022-08-07 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Technology 
 Phones 
 TEC-PH-10003645 
 220 
 260 
 2 
 2 
 
 
 9992 
 9993 
 2022-11-19 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Office Supplies 
 Paper 
 OFF-PA-10004041 
 30 
 30 
 4 
 3 
 
 
 9993 
 9994 
 2022-07-17 
 Second Class 
 Consumer 
 United States 
 Westminster 
 California 
 92683 
 West 
 Office Supplies 
 Appliances 
 OFF-AP-10002684 
 210 
 240 
 2 
 3 
 
 
 
 9994 rows × 16 columns

In [0]:
df_orders['discount']=df_orders['list_price']*df_orders['discount_percent']*.01
df_orders['sale_price']= df_orders['list_price']-df_orders['discount']
df_orders['profit']=df_orders['sale_price']-df_orders['cost_price']
df_orders

order_id 
 order_date 
 ship_mode 
 segment 
 country 
 city 
 state 
 postal_code 
 region 
 category 
 sub_category 
 product_id 
 cost_price 
 list_price 
 quantity 
 discount_percent 
 discount 
 sale_price 
 profit 
 
 
 
 
 0 
 1 
 2023-03-01 
 Second Class 
 Consumer 
 United States 
 Henderson 
 Kentucky 
 42420 
 South 
 Furniture 
 Bookcases 
 FUR-BO-10001798 
 240 
 260 
 2 
 2 
 5.2 
 254.8 
 14.8 
 
 
 1 
 2 
 2023-08-15 
 Second Class 
 Consumer 
 United States 
 Henderson 
 Kentucky 
 42420 
 South 
 Furniture 
 Chairs 
 FUR-CH-10000454 
 600 
 730 
 3 
 3 
 21.9 
 708.1 
 108.1 
 
 
 2 
 3 
 2023-01-10 
 Second Class 
 Corporate 
 United States 
 Los Angeles 
 California 
 90036 
 West 
 Office Supplies 
 Labels 
 OFF-LA-10000240 
 10 
 10 
 2 
 5 
 0.5 
 9.5 
 -0.5 
 
 
 3 
 4 
 2022-06-18 
 Standard Class 
 Consumer 
 United States 
 Fort Lauderdale 
 Florida 
 33311 
 South 
 Furniture 
 Tables 
 FUR-TA-10000577 
 780 
 960 
 5 
 2 
 19.2 
 940.8 
 160.8 
 
 
 4 
 5 
 2022-07-13 
 Standard Class 
 Consumer 
 United States 
 Fort Lauderdale 
 Florida 
 33311 
 South 
 Office Supplies 
 Storage 
 OFF-ST-10000760 
 20 
 20 
 2 
 5 
 1.0 
 19.0 
 -1.0 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 9989 
 9990 
 2023-02-18 
 Second Class 
 Consumer 
 United States 
 Miami 
 Florida 
 33180 
 South 
 Furniture 
 Furnishings 
 FUR-FU-10001889 
 30 
 30 
 3 
 4 
 1.2 
 28.8 
 -1.2 
 
 
 9990 
 9991 
 2023-03-17 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Furniture 
 Furnishings 
 FUR-FU-10000747 
 70 
 90 
 2 
 4 
 3.6 
 86.4 
 16.4 
 
 
 9991 
 9992 
 2022-08-07 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Technology 
 Phones 
 TEC-PH-10003645 
 220 
 260 
 2 
 2 
 5.2 
 254.8 
 34.8 
 
 
 9992 
 9993 
 2022-11-19 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Office Supplies 
 Paper 
 OFF-PA-10004041 
 30 
 30 
 4 
 3 
 0.9 
 29.1 
 -0.9 
 
 
 9993 
 9994 
 2022-07-17 
 Second Class 
 Consumer 
 United States 
 Westminster 
 California 
 92683 
 West 
 Office Supplies 
 Appliances 
 OFF-AP-10002684 
 210 
 240 
 2 
 3 
 7.2 
 232.8 
 22.8 
 
 
 
 9994 rows × 19 columns

###5. Convert order_date to DateTime Format and Drop Unnecessary Columns
We convert the order_date column to datetime format and drop columns that are no longer needed.

In [0]:
df_orders['order_date']=pd.to_datetime(df_orders['order_date'],format="%Y-%m-%d")

In [0]:
df_orders.drop(columns=['list_price','cost_price','discount_percent'],inplace=True)

In [0]:
df_orders

order_id 
 order_date 
 ship_mode 
 segment 
 country 
 city 
 state 
 postal_code 
 region 
 category 
 sub_category 
 product_id 
 quantity 
 discount 
 sale_price 
 profit 
 
 
 
 
 0 
 1 
 2023-03-01 
 Second Class 
 Consumer 
 United States 
 Henderson 
 Kentucky 
 42420 
 South 
 Furniture 
 Bookcases 
 FUR-BO-10001798 
 2 
 5.2 
 254.8 
 14.8 
 
 
 1 
 2 
 2023-08-15 
 Second Class 
 Consumer 
 United States 
 Henderson 
 Kentucky 
 42420 
 South 
 Furniture 
 Chairs 
 FUR-CH-10000454 
 3 
 21.9 
 708.1 
 108.1 
 
 
 2 
 3 
 2023-01-10 
 Second Class 
 Corporate 
 United States 
 Los Angeles 
 California 
 90036 
 West 
 Office Supplies 
 Labels 
 OFF-LA-10000240 
 2 
 0.5 
 9.5 
 -0.5 
 
 
 3 
 4 
 2022-06-18 
 Standard Class 
 Consumer 
 United States 
 Fort Lauderdale 
 Florida 
 33311 
 South 
 Furniture 
 Tables 
 FUR-TA-10000577 
 5 
 19.2 
 940.8 
 160.8 
 
 
 4 
 5 
 2022-07-13 
 Standard Class 
 Consumer 
 United States 
 Fort Lauderdale 
 Florida 
 33311 
 South 
 Office Supplies 
 Storage 
 OFF-ST-10000760 
 2 
 1.0 
 19.0 
 -1.0 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 9989 
 9990 
 2023-02-18 
 Second Class 
 Consumer 
 United States 
 Miami 
 Florida 
 33180 
 South 
 Furniture 
 Furnishings 
 FUR-FU-10001889 
 3 
 1.2 
 28.8 
 -1.2 
 
 
 9990 
 9991 
 2023-03-17 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Furniture 
 Furnishings 
 FUR-FU-10000747 
 2 
 3.6 
 86.4 
 16.4 
 
 
 9991 
 9992 
 2022-08-07 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Technology 
 Phones 
 TEC-PH-10003645 
 2 
 5.2 
 254.8 
 34.8 
 
 
 9992 
 9993 
 2022-11-19 
 Standard Class 
 Consumer 
 United States 
 Costa Mesa 
 California 
 92627 
 West 
 Office Supplies 
 Paper 
 OFF-PA-10004041 
 4 
 0.9 
 29.1 
 -0.9 
 
 
 9993 
 9994 
 2022-07-17 
 Second Class 
 Consumer 
 United States 
 Westminster 
 California 
 92683 
 West 
 Office Supplies 
 Appliances 
 OFF-AP-10002684 
 2 
 7.2 
 232.8 
 22.8 
 
 
 
 9994 rows × 16 columns

###6. Save the Cleaned DataFrame as CSV and Create a Spark DataFrame
We save the cleaned DataFrame as a CSV file and load it into a Spark DataFrame for further analysis.

In [0]:
df = df_orders.to_csv('orders.csv')

In [0]:
df = spark.createDataFrame(df_orders)

In [0]:
df

Out[46]: DataFrame[order_id: bigint, order_date: timestamp, ship_mode: string, segment: string, country: string, city: string, state: string, postal_code: bigint, region: string, category: string, sub_category: string, product_id: string, quantity: bigint, discount: double, sale_price: double, profit: double]

###7. Create a Temporary View for SQL Queries
We create a temporary view of the DataFrame to execute SQL queries.

In [0]:
df.createOrReplaceTempView('df')


In [0]:
%sql
select * from df

order_id order_date ship_mode segment country city state postal_code region category sub_category product_id quantity discount sale_price profit 1 2023-03-01T00:00:00.000+0000 Second Class Consumer United States Henderson Kentucky 42420 South Furniture Bookcases FUR-BO-10001798 2 5.2 254.8 14.800000000000011 2 2023-08-15T00:00:00.000+0000 Second Class Consumer United States Henderson Kentucky 42420 South Furniture Chairs FUR-CH-10000454 3 21.900000000000002 708.1 108.10000000000002 3 2023-01-10T00:00:00.000+0000 Second Class Corporate United States Los Angeles California 90036 West Office Supplies Labels OFF-LA-10000240 2 0.5 9.5 -0.5 4 2022-06-18T00:00:00.000+0000 Standard Class Consumer United States Fort Lauderdale Florida 33311 South Furniture Tables FUR-TA-10000577 5 19.2 940.8 160.79999999999995 5 2022-07-13T00:00:00.000+0000 Standard Class Consumer United States Fort Lauderdale Florida 33311 South Office Supplies Storage OFF-ST-10000760 2 1.0 19.0 -1.0 6 2022-03-13T00:00:00.000+0000 null Consumer United States Los Angeles California 90032 West Furniture Furnishings FUR-FU-10001487 7 1.5 48.5 -1.5 7 2022-12-28T00:00:00.000+0000 Standard Class Consumer United States Los Angeles California 90032 West Office Supplies Art OFF-AR-10002833 4 0.3 9.7 -0.3000000000000007 8 2022-01-25T00:00:00.000+0000 Standard Class Consumer United States Los Angeles California 90032 West Technology Phones TEC-PH-10002275 6 45.5 864.5 4.5 9 2023-03-23T00:00:00.000+0000 null Consumer United States Los Angeles California 90032 West Office Supplies Binders OFF-BI-10003910 3 0.4 19.6 -0.3999999999999986 10 2023-05-16T00:00:00.000+0000 Standard Class Consumer United States Los Angeles California 90032 West Office Supplies Appliances OFF-AP-10002892 5 3.3000000000000003 106.7 16.700000000000003 11 2023-03-31T00:00:00.000+0000 null Consumer United States Los Angeles California 90032 West Furniture Tables FUR-TA-10001539 9 51.300000000000004 1658.7 188.70000000000005 12 2023-12-25T00:00:00.000+0000 null Consumer United States Los Angeles California 90032 West Technology Phones TEC-PH-10002033 4 27.3 882.7 132.70000000000005 13 2022-02-11T00:00:00.000+0000 Standard Class Consumer United States Concord North Carolina 28027 South Office Supplies Paper OFF-PA-10002365 3 0.6 19.4 -0.6000000000000014 14 2023-07-18T00:00:00.000+0000 Standard Class Consumer United States Seattle Washington 98103 West Office Supplies Binders OFF-BI-10003656 3 8.2 401.8 41.80000000000001 15 2023-11-09T00:00:00.000+0000 null Home Office United States Fort Worth Texas 76106 Central Office Supplies Appliances OFF-AP-10002311 5 3.5 66.5 6.5 16 2022-06-18T00:00:00.000+0000 Standard Class Home Office United States Fort Worth Texas 76106 Central Office Supplies Binders OFF-BI-10000756 3 0.0 0.0 0.0 17 2022-02-04T00:00:00.000+0000 Standard Class Consumer United States Madison Wisconsin 53711 Central Office Supplies Storage OFF-ST-10004186 6 20.1 649.9 39.89999999999998 18 2023-08-04T00:00:00.000+0000 Second Class Consumer United States West Jordan Utah 84084 West Office Supplies Storage OFF-ST-10000107 2 2.4 57.6 -2.3999999999999986 19 2022-01-23T00:00:00.000+0000 Second Class Consumer United States San Francisco California 94109 West Office Supplies Art OFF-AR-10003056 2 0.4 9.6 -0.40000000000000036 20 2022-01-11T00:00:00.000+0000 Second Class Consumer United States San Francisco California 94109 West Technology Phones TEC-PH-10001949 3 6.3 203.7 33.69999999999999 21 2022-10-05T00:00:00.000+0000 Second Class Consumer United States San Francisco California 94109 West Office Supplies Binders OFF-BI-10002215 4 0.4 19.6 -0.3999999999999986 22 2023-07-16T00:00:00.000+0000 Standard Class Corporate United States Fremont Nebraska 68025 Central Office Supplies Art OFF-AR-10000246 7 0.8 19.2 -0.8000000000000007 23 2023-05-06T00:00:00.000+0000 Standard Class Corporate United States Fremont Nebraska 68025 Central Office Supplies Appliances OFF-AP-10001492 7 1.8 58.2 8.200000000000003 24 2023-05-21T

####8. SQL Queries for Data Analysis
8.1. Find Top 10 Highest Revenue Generating Products

In [0]:
%sql
--find top 10 highest reveue generating products 
select product_id,round(sum(sale_price*quantity),0) as total_sales from df
group by product_id 
order by total_sales desc 
limit 10

product_id total_sales TEC-CO-10004722 245056.0 OFF-BI-10000545 163778.0 TEC-MA-10002412 130406.0 FUR-CH-10002024 120091.0 TEC-PH-10001459 113042.0 TEC-CO-10001449 107388.0 OFF-BI-10003527 97083.0 TEC-MA-10000822 89622.0 FUR-BO-10002213 84015.0 TEC-MA-10001047 81549.0

8.2. Find Top 5 Highest Selling Products in Each Region



In [0]:
%sql
--find top 5 highest selling products in each region
with cte as (
select product_id,region, row_number()over(partition by region order by sum(sale_price*quantity) desc) as rn,
sum(sale_price*quantity) as sales 
from df as orders
group by product_id,region 
)
select * from cte 
where rn<6

product_id region rn sales OFF-BI-10000545 Central 1 125827.5 TEC-CO-10004722 Central 2 84875.0 TEC-MA-10000822 Central 3 77509.79999999999 OFF-BI-10001120 Central 4 55282.5 OFF-BI-10004995 Central 5 42210.0 TEC-CO-10004722 East 1 106421.0 TEC-MA-10001047 East 2 81549.0 FUR-BO-10004834 East 3 66364.2 TEC-CO-10001449 East 4 60948.0 FUR-CH-10002024 East 5 60189.6 TEC-MA-10002412 South 1 130406.40000000001 TEC-PH-10001459 South 2 73932.1 FUR-TA-10000198 South 3 68789.9 TEC-MA-10001127 South 4 50499.2 OFF-BI-10003527 South 5 32029.4 TEC-AC-10003832 West 1 61170.8 TEC-CO-10004722 West 2 53760.0 OFF-SU-10000151 West 3 53337.9 FUR-TA-10003473 West 4 52669.49999999999 FUR-CH-10003973 West 5 43596.4

8.3. Month Over Month Growth Comparison for 2022 and 2023 Sales



In [0]:
%sql
--find month over month growth comparison for 2022 and 2023 sales eg : jan 2022 vs jan 2023
with cte as(
select year(order_date) as order_year,month(order_date) as order_month ,sum(sale_price) as sales
from df as orders
group by year(order_date),month(order_date)
order by year(order_date),month(order_date)
)
select order_month,
sum(case when order_year=2022 then floor(sales) else 0 end) as sales_2022,
sum(case when order_year=2023 then floor(sales) else 0 end) as sales_2023
from cte 
group by order_month


order_month sales_2022 sales_2023 12 95869 102556 1 94712 88632 6 94170 68976 3 80106 82512 5 79448 86447 9 79142 76658 4 95451 111568 8 104808 87733 7 78652 90563 10 118912 121061 11 84225 75432 2 90091 128124

8.4. For Each Category, Find Which Month Had Highest Sales



In [0]:
%sql
--for each category which month had highest sales 
with cte as(
select distinct category,year(order_date) as order_year,month(order_date) as order_month,
row_number()over(partition by category,year(order_date) order by sum(sale_price) desc) as rn,
sum(sale_price) as sales
from df as orders
group by year(order_date),month(order_date),category)
select *
from cte
where rn=1

category order_year order_month rn sales Office Supplies 2023 2 1 44118.5 Technology 2022 10 1 50021.0 Furniture 2023 8 1 42231.8 Office Supplies 2022 4 1 40114.7 Furniture 2022 10 1 42888.9 Technology 2023 10 1 53000.1

8.5. Sub-category with Highest Growth in Profit in 2023 Compared to 2022



In [0]:
%sql
--which sub category had highest growth by profit in 2023 compare to 2022
with cte as (
select sub_category,year(order_date) as order_year,
sum(sale_price) as sales
from df
group by sub_category,year(order_date)
--order by year(order_date),month(order_date)
	)
, cte2 as (
select sub_category
, sum(case when order_year=2022 then sales else 0 end) as sales_2022
, sum(case when order_year=2023 then sales else 0 end) as sales_2023
from cte 
group by sub_category
)
select *
,(sales_2023-sales_2022)
from  cte2
order by (sales_2023-sales_2022) desc
limit 1

sub_category sales_2022 sales_2023 (sales_2023 - sales_2022) Machines 73723.2 109178.50000000001 35455.30000000002